In [1]:
import wandb
import pandas as pd
import pandas_profiling

run = wandb.init(project="nyc_airbnb", group="eda", save_code=True)

Failed to detect the name of this notebook, you can set it manually with the WANDB_NOTEBOOK_NAME environment variable to enable code saving.
wandb: Currently logged in as: adsmaniotto (use `wandb login --relogin` to force relogin)
wandb: wandb version 0.12.6 is available!  To upgrade, please run:
wandb:  $ pip install wandb --upgrade


## Data Import
Using the artifact path in W&B, let's import the sample CSV to a dataframe.

In [2]:
local_path = wandb.use_artifact("sample.csv:latest").file()
df = pd.read_csv(local_path)

## Data Cleanup
Next, we'll clean up the dataset by dropping any rows with an "outlier" price. We'll also convert our timestamp column `last_review` to datetime.

In [3]:
# Drop outliers
min_price = 10
max_price = 350
idx = df['price'].between(min_price, max_price)
df = df[idx].copy()

# Convert last_review to datetime
df['last_review'] = pd.to_datetime(df['last_review'])



## Exploratory analysis
Let's run a pandas profile on the cleaned-up data for some descriptive statistics.

In [6]:
profile = pandas_profiling.ProfileReport(df)
profile.to_notebook_iframe()

Render HTML: 100%|██████████| 1/1 [00:03<00:00,  3.84s/it]


Insights from the pandas profile:
- Two columns have a high prevalence of zero values (`number_of_reviews` and `availability_365`)
- Highly skewed data for the `minimum_nights` feature
- Missing values for `last_review` and `reviews_per_month`
- There is some correlation between `latitute`/`longitude` and price, giving us an indication of where in NYC we might see rental commanding higher prices

In [7]:
run.finish()